In [1]:
# Experiment 2 Script for COVID-19 Forecasting
# Change path to the root directory of the project
import os
os.chdir("../../")

# Description: This script contains the code for the second experiment in the project, 
# forecasting COVID-19 MVBeds using various RNN models and hyperparameter tuning with Simulated Annealing.

# Imports for handling data
import shutil
import numpy as np
import pandas as pd
from pathlib import Path
from itertools import cycle

# Imports for machine learning
import torch
from torch.utils.data import Dataset, DataLoader
import pytorch_lightning as pl
from pytorch_lightning.callbacks import EarlyStopping

from sklearn.metrics import mean_absolute_error as mae, mean_squared_error as mse

# Imports for visualization
import plotly.express as px
import plotly.graph_objects as go

# Progress bar
from tqdm.autonotebook import tqdm
tqdm.pandas()

# Local imports for data loaders and models
from src.utils import plotting_utils
from src.dl.dataloaders import TimeSeriesDataModule
from src.dl.multivariate_models import SingleStepRNNConfig, SingleStepRNNModel, Seq2SeqConfig, Seq2SeqModel, RNNConfig
from src.transforms.target_transformations import AutoStationaryTransformer

# Set seeds for reproducibility
pl.seed_everything(42)
torch.manual_seed(42)
np.random.seed(42)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(42)

torch.set_float32_matmul_precision('high')

# Set default plotly template
import plotly.io as pio
pio.templates.default = "plotly_white"

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")
import logging

# Set logging configuration
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')


Global seed set to 42


In [2]:
# Utility Functions

def format_plot(fig, legends=None, xlabel="Time", ylabel="Value", title="", font_size=15):
    if legends:
        names = cycle(legends)
        fig.for_each_trace(lambda t: t.update(name=next(names)))
    fig.update_layout(
        autosize=False,
        width=900,
        height=500,
        title_text=title,
        title={"x": 0.5, "xanchor": "center", "yanchor": "top"},
        titlefont={"size": 20},
        legend_title=None,
        legend=dict(
            font=dict(size=font_size),
            orientation="h",
            yanchor="bottom",
            y=0.98,
            xanchor="right",
            x=1,
        ),
        yaxis=dict(
            title_text=ylabel,
            titlefont=dict(size=font_size),
            tickfont=dict(size=font_size),
        ),
        xaxis=dict(
            title_text=xlabel,
            titlefont=dict(size=font_size),
            tickfont=dict(size=font_size),
        ),
    )
    return fig

def mase(actual, predicted, insample_actual):
    mae_insample = np.mean(np.abs(np.diff(insample_actual)))
    mae_outsample = np.mean(np.abs(actual - predicted))
    return mae_outsample / mae_insample

def forecast_bias(actual, predicted):
    return np.mean(predicted - actual)

def plot_forecast(pred_df, forecast_columns, selected_area, forecast_display_names=None, save_path=None):
    if forecast_display_names is None:
        forecast_display_names = forecast_columns
    else:
        assert len(forecast_columns) == len(forecast_display_names)

    mask = ~pred_df[forecast_columns[0]].isnull()
    colors = px.colors.qualitative.D3  # Use a colorblind-friendly palette
    act_color = colors[0]
    colors = cycle(colors[1:])

    fig = go.Figure()

    # Actual data plot
    fig.add_trace(
        go.Scatter(
            x=pred_df[mask].index,
            y=pred_df[mask].covidOccupiedMVBeds,
            mode="lines+markers",
            marker=dict(size=8, opacity=0.7, symbol='circle'),
            line=dict(color=act_color, width=3),
            name="Actual COVID-19 MVBeds trends",
        )
    )

    # Predicted data plot
    line_styles = ["solid", "dash", "dot", "dashdot"]
    markers = ['circle', 'square', 'diamond', 'cross', 'x', 'triangle-up']
    for col, display_col, line_style, marker in zip(forecast_columns, forecast_display_names, cycle(line_styles), cycle(markers)):
        fig.add_trace(
            go.Scatter(
                x=pred_df[mask].index,
                y=pred_df.loc[mask, col],
                mode="lines+markers",
                marker=dict(size=6, symbol=marker),
                line=dict(color=next(colors), width=2, dash=line_style),
                name=display_col,
            )
        )

    fig.update_layout(
        title=f"COVID-19 MVBeds Forecast Comparison for {selected_area}",
        title_font=dict(size=20),
        xaxis_title="Date",
        yaxis_title="COVID-19 MVBeds",
        xaxis=dict(title_font=dict(size=15), tickfont=dict(size=12)),
        yaxis=dict(title_font=dict(size=15), tickfont=dict(size=12)),
        legend=dict(
            font=dict(size=10),
            orientation="h",
            yanchor="top",
            y=1.02,  # Move the legend down to separate it from the title
            xanchor="center",
            x=0.5
        ),
        template="plotly_white",
        plot_bgcolor="rgba(0,0,0,0)",
        margin=dict(l=10, r=40, t=80, b=40),  # Adjust left margin for better alignment
        width=1200,
        height=600
    )

    if save_path:
        pio.write_image(fig, save_path)
    return fig


def highlight_abs_min(s, props=""):
    return np.where(s == np.nanmin(np.abs(s.values)), props, "")

# Function to convert data to float32
def to_float32(df):
    for col in df.columns:
        df[col] = df[col].astype("float32")
    return df

In [3]:
# # Load and Prepare Data
# data_path = Path("data/hos_data/england_data.csv")
# # data = pd.read_csv(data_path).drop("Unnamed: 0", axis=1)
# data = pd.read_csv(data_path)
# data["date"] = pd.to_datetime(data["date"])

# # Select and Process Data
# selected_area = "England"
# # data_filtered = data[data["areaName"] == selected_area]
# data_filtered = data.copy()
# # Data Processing
# data_filtered["date"] = pd.to_datetime(data_filtered["date"])
# data_filtered.sort_values(by=["date", "areaName"], inplace=True)
# Load and Prepare Data
data_path = Path("data/hos_data/merged_data.csv")
data = pd.read_csv(data_path)

data["date"] = pd.to_datetime(data["date"])

# Select and Process Data
selected_area = "London"
data_filtered = data[data["nhs_region"] == selected_area]

# Data Processing
data_filtered["date"] = pd.to_datetime(data_filtered["date"])

data_filtered.drop(
    [
        # "areaName",
        # "areaCode",
        "areaCode",
        "region_x",
        "areaType",
        "nhs_region",
        "cumAdmissions",
        "cumulative_confirmed",
        "cumulative_deceased",
        "population",
        "openstreetmap_id",
        "latitude",
        "longitude",
        "region_y",
        "epi_week",
        # "latitude",
        # "longitude",
        # "epi_week",
    ],
    axis=1,
    inplace=True,
)

# flip the data
data_filtered = data_filtered[::-1].reset_index(drop=True)
data_filtered.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 894 entries, 0 to 893
Data columns (total 6 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   date                 894 non-null    datetime64[ns]
 1   covidOccupiedMVBeds  894 non-null    float64       
 2   hospitalCases        894 non-null    float64       
 3   newAdmissions        894 non-null    int64         
 4   new_confirmed        894 non-null    float64       
 5   new_deceased         894 non-null    float64       
dtypes: datetime64[ns](1), float64(4), int64(1)
memory usage: 42.0 KB


In [4]:
data_filtered.head()

date  covidOccupiedMVBeds  hospitalCases  newAdmissions  \
0 2020-04-01                  0.0         4219.0            767   
1 2020-04-02                673.0         4168.0            835   
2 2020-04-03                759.0         4092.0            647   
3 2020-04-04                824.0         4691.0            733   
4 2020-04-05                800.0         4869.0            732   

   new_confirmed  new_deceased  
0          977.0         189.0  
1         1063.0         193.0  
2          985.0         192.0  
3          765.0         225.0  
4          636.0         196.0

In [5]:
# Add time-lagged features
def add_lags(data, lags, features):
    added_features = []
    for feature in features:
        for lag in lags:
            new_feature = feature + f"_lag_{lag}"
            data[new_feature] = data[feature].shift(lag)
            added_features.append(new_feature)
    return data, added_features


lags = [1, 2, 3, 5, 7, 14, 21]
data_filtered, added_features = add_lags(data_filtered, lags, ["covidOccupiedMVBeds"])
data_filtered.dropna(inplace=True)


# Create temporal features
def create_temporal_features(df, date_column):
    df["month"] = df[date_column].dt.month
    df["day"] = df[date_column].dt.day
    df["day_of_week"] = df[date_column].dt.dayofweek
    return df


data_filtered = create_temporal_features(data_filtered, "date")
data_filtered = data_filtered.set_index("date")

In [6]:
# Load and process the SEIRD data
# merged_data = data_filtered.copy()
seird_data = pd.read_csv(f"reports/output/pinn_{selected_area}_output.csv")
seird_data["date"] = pd.to_datetime(seird_data["date"])
seird_data.set_index("date", inplace=True)

# Merge the two dataframes on the date index
merged_data = pd.merge(
    data_filtered, seird_data, left_index=True, right_index=True, how="inner"
)

# Drop rows with any missing values
merged_data.dropna(inplace=True)
merged_data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 396 entries, 2020-05-01 to 2021-05-31
Data columns (total 20 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   covidOccupiedMVBeds         396 non-null    float64
 1   hospitalCases               396 non-null    float64
 2   newAdmissions               396 non-null    int64  
 3   new_confirmed               396 non-null    float64
 4   new_deceased                396 non-null    float64
 5   covidOccupiedMVBeds_lag_1   396 non-null    float64
 6   covidOccupiedMVBeds_lag_2   396 non-null    float64
 7   covidOccupiedMVBeds_lag_3   396 non-null    float64
 8   covidOccupiedMVBeds_lag_5   396 non-null    float64
 9   covidOccupiedMVBeds_lag_7   396 non-null    float64
 10  covidOccupiedMVBeds_lag_14  396 non-null    float64
 11  covidOccupiedMVBeds_lag_21  396 non-null    float64
 12  month                       396 non-null    int64  
 13  day             

In [7]:
merged_data.head()

covidOccupiedMVBeds  hospitalCases  newAdmissions  new_confirmed  \
date                                                                           
2020-05-01                712.0         2596.0            201          355.0   
2020-05-02                678.0         2432.0            150          248.0   
2020-05-03                638.0         2390.0            157          170.0   
2020-05-04                587.0         2328.0            169          245.0   
2020-05-05                565.0         2270.0            178          216.0   

            new_deceased  covidOccupiedMVBeds_lag_1  \
date                                                  
2020-05-01          42.0                      723.0   
2020-05-02          52.0                      712.0   
2020-05-03          43.0                      678.0   
2020-05-04          37.0                      638.0   
2020-05-05          34.0                      587.0   

            covidOccupiedMVBeds_lag_2  covidOccupiedMVBeds_lag_3  \
date                                                               
2020-05-01                      733.0                      755.0   
2020-05-02                      723.0                      733.0   
2020-05-03                      712.0                      723.0   
2020-05-04                      678.0                      712.0   
2020-05-05                      638.0                      678.0   

            covidOccupiedMVBeds_lag_5  covidOccupiedMVBeds_lag_7  \
date                                                               
2020-05-01                      831.0                      836.0   
2020-05-02                      800.0                      868.0   
2020-05-03                      755.0                      831.0   
2020-05-04                      733.0                      800.0   
2020-05-05                      723.0                      755.0   

            covidOccupiedMVBeds_lag_14  covidOccupiedMVBeds_lag_21  month  \
date                                                                        
2020-05-01                       982.0                      1057.0      5   
2020-05-02                       992.0                      1035.0      5   
2020-05-03                       991.0                      1035.0      5   
2020-05-04                      1019.0                      1046.0      5   
2020-05-05                       972.0                      1026.0      5   

            day  day_of_week  susceptible       exposed  active_cases  \
date                                                                    
2020-05-01    1            4    8954095.0    -12.285504     22690.895   
2020-05-02    2            5    8950943.0  13936.139000     22516.533   
2020-05-03    3            6    8957262.0  17855.506000     23400.936   
2020-05-04    4            0    8954641.0  18558.420000     22969.748   
2020-05-05    5            1    8953184.0  20188.898000     22702.023   

              recovered  cumulative_deceased  
date                                          
2020-05-01   -32.613026            5506.8027  
2020-05-02  1638.377900            5508.5230  
2020-05-03 -4881.178700            5544.7360  
2020-05-04   -88.820175            5554.4910  
2020-05-05  -738.019300            5605.8100

In [8]:
merged_data.to_csv("data/hos_data/merged_data_gpt.csv")

In [9]:
# from sklearn.preprocessing import MinMaxScaler


# # Adjust the list of features to exclude the missing columns
# adjusted_features = [
#     "covidOccupiedMVBeds",
#     "covidOccupiedMVBeds_lag_1",
#     "covidOccupiedMVBeds_lag_2",
#     "covidOccupiedMVBeds_lag_3",
#     "covidOccupiedMVBeds_lag_5",
#     "covidOccupiedMVBeds_lag_7",
#     "covidOccupiedMVBeds_lag_14",
#     "covidOccupiedMVBeds_lag_21",
#     "month",
#     "day",
#     "day_of_week",
#     "susceptible",
#     "exposed",
#     "active_cases",
#     "recovered",
#     "cumulative_deceased"
# ]


# # Initialize the scaler
# scaler = MinMaxScaler()



# # Fit and transform the data
# data_scaled = pd.DataFrame(scaler.fit_transform(merged_data[adjusted_features]), columns=adjusted_features)

# # Display the first few rows of the scaled data
# data_scaled.head()


In [10]:
# import numpy as np
# from sklearn.model_selection import train_test_split
# from tensorflow.keras.models import Sequential
# from tensorflow.keras.layers import Dense, SimpleRNN
# from tensorflow.keras.optimizers import Adam

# # Prepare the data
# X = data_scaled.drop(columns=["covidOccupiedMVBeds"]).values
# y = data_scaled["covidOccupiedMVBeds"].values

# # Split the data into training and testing sets
# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# # Reshape the data to fit the RNN input format (samples, time steps, features)
# X_train = np.reshape(X_train, (X_train.shape[0], 1, X_train.shape[1]))
# X_test = np.reshape(X_test, (X_test.shape[0], 1, X_test.shape[1]))

# # Build the RNN model
# model = Sequential()
# model.add(SimpleRNN(50, activation='relu', input_shape=(X_train.shape[1], X_train.shape[2])))
# model.add(Dense(1))

# # Compile the model
# model.compile(optimizer=Adam(learning_rate=0.001), loss='mean_squared_error', metrics=['mae'])

# # Train the model
# history = model.fit(X_train, y_train, epochs=50, batch_size=32, validation_split=0.1, verbose=2)

# # Evaluate the model
# train_loss, train_mae = model.evaluate(X_train, y_train, verbose=0)
# test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)

# print(f"Train Loss: {train_loss}, Train MAE: {train_mae}")
# print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")


In [11]:
# import matplotlib.pyplot as plt

# # Make predictions
# y_train_pred = model.predict(X_train)
# y_test_pred = model.predict(X_test)

# # Function to rescale the predicted values
# def rescale_predictions(predictions, X, scaler, original_features):
#     # Create a placeholder array for rescaling
#     rescaled_predictions = np.zeros((predictions.shape[0], len(original_features)))
#     rescaled_predictions[:, 0] = predictions[:, 0]  # Put predictions in the first column
#     # Use the remaining columns from the input features to rescale properly
#     rescaled_predictions[:, 1:X.shape[2]] = X[:, 0, 1:]
#     # Inverse transform using the scaler
#     rescaled_predictions = scaler.inverse_transform(rescaled_predictions)
#     return rescaled_predictions[:, 0]  # Return only the first column (rescaled predictions)

# # Original features used for scaling
# original_features = adjusted_features

# # Rescale the predictions and actual values
# y_train_pred_rescaled = rescale_predictions(y_train_pred, X_train, scaler, original_features)
# y_test_pred_rescaled = rescale_predictions(y_test_pred, X_test, scaler, original_features)
# y_train_rescaled = rescale_predictions(y_train.reshape(-1, 1), X_train, scaler, original_features)
# y_test_rescaled = rescale_predictions(y_test.reshape(-1, 1), X_test, scaler, original_features)

# # Plot the actual vs predicted values for the test set
# plt.figure(figsize=(14, 7))
# plt.plot(y_test_rescaled, label='Actual')
# plt.plot(y_test_pred_rescaled, label='Predicted')
# plt.title('Actual vs Predicted covidOccupiedMVBeds')
# plt.xlabel('Time')
# plt.ylabel('covidOccupiedMVBeds')
# plt.legend()
# plt.show()


In [12]:
# def create_windowed_dataset(data, target_column, window_size=7):
#     X, y = [], []
#     for i in range(len(data) - window_size):
#         X.append(data[i:i+window_size].drop(columns=[target_column]).values)
#         y.append(data[target_column].values[i + window_size])
#     return np.array(X), np.array(y)

# # Prepare the data
# target_column = "covidOccupiedMVBeds"
# window_size = 7

# # Create windowed sequences
# X_windowed, y_windowed = create_windowed_dataset(data_scaled, target_column, window_size)

# # Split the data into training and testing sets
# X_train, X_test, y_train, y_test = train_test_split(X_windowed, y_windowed, test_size=0.2, random_state=42)

# # Reshape the data to fit the RNN input format (samples, time steps, features)
# X_train = np.reshape(X_train, (X_train.shape[0], window_size, X_train.shape[2]))
# X_test = np.reshape(X_test, (X_test.shape[0], window_size, X_test.shape[2]))


In [13]:
# from tensorflow.keras.layers import LSTM

# # Build a 5 layer LSTM model
# model = Sequential()
# model.add(LSTM(50, activation='relu', return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
# model.add(LSTM(50, activation='relu', return_sequences=True))
# model.add(LSTM(50, activation='relu', return_sequences=True))
# model.add(LSTM(50, activation='relu', return_sequences=True))
# model.add(LSTM(50, activation='relu'))
# model.add(Dense(1))

# # Compile the model
# model.compile(optimizer=Adam(learning_rate=0.001), loss='mean_squared_error', metrics=['mae'])

# # Train the model
# history = model.fit(X_train, y_train, epochs=50, batch_size=32, validation_split=0.1, verbose=2)

# # Evaluate the model
# train_loss, train_mae = model.evaluate(X_train, y_train, verbose=0)
# test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)

# train_loss, train_mae, test_loss, test_mae


In [14]:
# import numpy as np
# import pandas as pd
# from sklearn.preprocessing import MinMaxScaler
# from sklearn.model_selection import train_test_split
# from tensorflow.keras.models import Sequential
# from tensorflow.keras.layers import LSTM, Dense, Dropout, BatchNormalization
# from tensorflow.keras.optimizers import Adam
# from sklearn.metrics import mean_squared_error, mean_absolute_error
# import matplotlib.pyplot as plt
# # Adjust the list of features to exclude the missing columns
# adjusted_features = [
#     "covidOccupiedMVBeds",
#     "covidOccupiedMVBeds_lag_1",
#     "covidOccupiedMVBeds_lag_2",
#     "covidOccupiedMVBeds_lag_3",
#     "covidOccupiedMVBeds_lag_5",
#     "covidOccupiedMVBeds_lag_7",
#     "covidOccupiedMVBeds_lag_14",
#     "covidOccupiedMVBeds_lag_21",
#     "month",
#     "day",
#     "day_of_week",
#     "susceptible",
#     "exposed",
#     "active_cases",
#     "recovered",
#     "cumulative_deceased"
# ]

# # Load the data (assuming the merged_data is already loaded as a DataFrame)
# merged_data = pd.read_csv('../../data/hos_data/merged_data_gpt.csv')

# # Initialize the scaler
# scaler = MinMaxScaler()

# # Fit and transform the data
# data_scaled = pd.DataFrame(scaler.fit_transform(merged_data[adjusted_features]), columns=adjusted_features)

# # Create windowed sequences for training and testing
# def create_windowed_dataset(data, target_column, window_size=7):
#     X, y = [], []
#     for i in range(len(data) - window_size):
#         X.append(data[i:i+window_size].drop(columns=[target_column]).values)
#         y.append(data[target_column].values[i + window_size])
#     return np.array(X), np.array(y)

# # Prepare the data
# target_column = "covidOccupiedMVBeds"
# window_size = 7

# # Create windowed sequences
# X_windowed, y_windowed = create_windowed_dataset(data_scaled, target_column, window_size)

# # Split the data into training and testing sets since it is a time series data
# X_train, X_test, y_train, y_test = train_test_split(X_windowed, y_windowed, test_size=0.2, shuffle=False)

# # Reshape the data to fit the RNN input format (samples, time steps, features)
# X_train = np.reshape(X_train, (X_train.shape[0], window_size, X_train.shape[2]))
# X_test = np.reshape(X_test, (X_test.shape[0], window_size, X_test.shape[2]))

# # Build the enhanced LSTM model
# model = Sequential()
# model.add(LSTM(100, activation='relu', return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu', return_sequences=True))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu', return_sequences=True))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu'))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(Dense(1))

# # Compile the model
# model.compile(optimizer=Adam(learning_rate=0.001), loss='mean_squared_error', metrics=['mae'])

# # Train the model
# history = model.fit(X_train, y_train, epochs=100, batch_size=32, validation_split=0.1, verbose=2)

# # Evaluate the model
# train_loss, train_mae = model.evaluate(X_train, y_train, verbose=0)
# test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)

# print(f"Train Loss: {train_loss}, Train MAE: {train_mae}")
# print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")

# # Make predictions
# y_train_pred = model.predict(X_train)
# y_test_pred = model.predict(X_test)

# def rescale_predictions(predictions, X, scaler, original_features):
#     # Create a placeholder array for rescaling
#     rescaled_predictions = np.zeros((predictions.shape[0], len(original_features)))
#     rescaled_predictions[:, 0] = predictions[:, 0]  # Put predictions in the first column
#     # Use the remaining columns from the input features to rescale properly
#     rescaled_predictions[:, 1:X.shape[2]] = X[:, 0, 1:]
#     # Inverse transform using the scaler
#     rescaled_predictions = scaler.inverse_transform(rescaled_predictions)
#     return rescaled_predictions[:, 0]  # Return only the first column (rescaled predictions)

# # Original features used for scaling
# original_features = adjusted_features

# # # Function to rescale the predicted values
# # def rescale_predictions(predictions, X, scaler, original_features):
# #     num_features = len(original_features)
# #     rescaled_predictions = np.zeros((predictions.shape[0], num_features))
# #     rescaled_predictions[:, 0] = predictions[:, 0]
# #     rescaled_predictions[:, 1:] = X[:, -1, :-1]
# #     rescaled_predictions_full = scaler.inverse_transform(rescaled_predictions)
# #     return rescaled_predictions_full[:, 0]

# # # Original features used for scaling
# # original_features = adjusted_features

# # Rescale the predictions and actual values
# y_train_pred_rescaled = rescale_predictions(y_train_pred, X_train, scaler, original_features)
# y_test_pred_rescaled = rescale_predictions(y_test_pred, X_test, scaler, original_features)
# y_train_rescaled = rescale_predictions(y_train.reshape(-1, 1), X_train, scaler, original_features)
# y_test_rescaled = rescale_predictions(y_test.reshape(-1, 1), X_test, scaler, original_features)

# # Calculate MAE and MSE on the original scale
# train_mae_original = mean_absolute_error(y_train_rescaled, y_train_pred_rescaled)
# test_mae_original = mean_absolute_error(y_test_rescaled, y_test_pred_rescaled)
# train_mse_original = mean_squared_error(y_train_rescaled, y_train_pred_rescaled)
# test_mse_original = mean_squared_error(y_test_rescaled, y_test_pred_rescaled)

# print(f"Train MAE (original scale): {train_mae_original}")
# print(f"Test MAE (original scale): {test_mae_original}")
# print(f"Train MSE (original scale): {train_mse_original}")
# print(f"Test MSE (original scale): {test_mse_original}")

# # Plot the actual vs predicted values for the test set
# plt.figure(figsize=(14, 7))
# plt.plot(y_test_rescaled, label='Actual')
# plt.plot(y_test_pred_rescaled, label='Predicted')
# plt.title('Actual vs Predicted covidOccupiedMVBeds')
# plt.xlabel('Time')
# plt.ylabel('covidOccupiedMVBeds')
# plt.legend()
# plt.show()


In [15]:
# import numpy as np
# import pandas as pd
# from sklearn.preprocessing import MinMaxScaler
# from sklearn.model_selection import train_test_split
# from tensorflow.keras.models import Sequential
# from tensorflow.keras.layers import LSTM, Dense, Dropout, BatchNormalization
# from tensorflow.keras.optimizers import Adam
# from tensorflow.keras.preprocessing.sequence import TimeseriesGenerator
# from sklearn.metrics import mean_squared_error, mean_absolute_error
# import matplotlib.pyplot as plt

# # Adjust the list of features to exclude the missing columns
# adjusted_features = [
#     "covidOccupiedMVBeds",
#     "covidOccupiedMVBeds_lag_1",
#     "covidOccupiedMVBeds_lag_2",
#     "covidOccupiedMVBeds_lag_3",
#     "covidOccupiedMVBeds_lag_5",
#     "covidOccupiedMVBeds_lag_7",
#     "covidOccupiedMVBeds_lag_14",
#     "covidOccupiedMVBeds_lag_21",
#     "month",
#     "day",
#     "day_of_week",
#     "susceptible",
#     "exposed",
#     "active_cases",
#     "recovered",
#     "cumulative_deceased"
# ]

# # Load the data
# merged_data = pd.read_csv('../../data/hos_data/merged_data_gpt.csv')

# # Initialize the scaler
# scaler = MinMaxScaler()

# # Fit and transform the data
# data_scaled = pd.DataFrame(scaler.fit_transform(merged_data[adjusted_features]), columns=adjusted_features)

# # Prepare the data
# target_column = "covidOccupiedMVBeds"
# window_size = 7
# batch_size = 32

# # Split the data into training and testing sets without shuffling
# train_size = int(len(data_scaled) * 0.8)
# train, test = data_scaled.iloc[:train_size], data_scaled.iloc[train_size:]

# # Create TimeseriesGenerator for training and testing
# train_generator = TimeseriesGenerator(train.drop(columns=[target_column]).values, train[target_column].values,
#                                       length=window_size, batch_size=batch_size)
# test_generator = TimeseriesGenerator(test.drop(columns=[target_column]).values, test[target_column].values,
#                                      length=window_size, batch_size=batch_size)

# # Build the enhanced LSTM model
# model = Sequential()
# model.add(LSTM(100, activation='relu', return_sequences=True, input_shape=(window_size, len(adjusted_features) - 1)))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu', return_sequences=True))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu', return_sequences=True))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(LSTM(100, activation='relu'))
# model.add(BatchNormalization())
# model.add(Dropout(0.2))

# model.add(Dense(1))

# # Compile the model
# model.compile(optimizer=Adam(learning_rate=0.001), loss='mean_squared_error', metrics=['mae'])

# # Train the model
# history = model.fit(train_generator, epochs=100, validation_data=test_generator, verbose=2)

# # Evaluate the model
# train_loss, train_mae = model.evaluate(train_generator, verbose=0)
# test_loss, test_mae = model.evaluate(test_generator, verbose=0)

# print(f"Train Loss: {train_loss}, Train MAE: {train_mae}")
# print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")
# # Make predictions
# y_train_pred = model.predict(train_generator)
# y_test_pred = model.predict(test_generator)

# # Reshape predictions to match original shape
# y_train_pred = y_train_pred.reshape(-1)
# y_test_pred = y_test_pred.reshape(-1)

# # Function to rescale the predicted values
# def rescale_predictions(predictions, generator, scaler, original_features):
#     rescaled_predictions = np.zeros((len(predictions), len(original_features)))
#     rescaled_predictions[:, 0] = predictions
#     rescaled_predictions[:, 1:] = generator.data[-len(predictions):, 1:]
#     rescaled_predictions = scaler.inverse_transform(rescaled_predictions)
#     return rescaled_predictions[:, 0]

# # Original features used for scaling
# original_features = adjusted_features

# # Rescale the predictions and actual values
# y_train_pred_rescaled = rescale_predictions(y_train_pred, train_generator, scaler, original_features)
# y_test_pred_rescaled = rescale_predictions(y_test_pred, test_generator, scaler, original_features)
# y_train_rescaled = rescale_predictions(train_generator.targets, train_generator, scaler, original_features)
# y_test_rescaled = rescale_predictions(test_generator.targets, test_generator, scaler, original_features)

# # Calculate MAE and MSE on the original scale
# train_mae_original = mean_absolute_error(y_train_rescaled, y_train_pred_rescaled)
# test_mae_original = mean_absolute_error(y_test_rescaled, y_test_pred_rescaled)
# train_mse_original = mean_squared_error(y_train_rescaled, y_train_pred_rescaled)
# test_mse_original = mean_squared_error(y_test_rescaled, y_test_pred_rescaled)


# print(f"Train MAE (original scale): {train_mae_original}")
# print(f"Test MAE (original scale): {test_mae_original}")
# print(f"Train MSE (original scale): {train_mse_original}")
# print(f"Test MSE (original scale): {test_mse_original}")

# # Plot the actual vs predicted values for the test set
# plt.figure(figsize=(14, 7))
# plt.plot(y_test_actual_rescaled, label='Actual')
# plt.plot(y_test_rescaled, label='Predicted')
# plt.title('Actual vs Predicted covidOccupiedMVBeds')
# plt.xlabel('Time')
# plt.ylabel('covidOccupiedMVBeds')
# plt.legend()
# plt.show()

In [16]:
# target_column = 'covidOccupiedMVBeds'
# rolling_window = 7

# # Apply rolling mean to all columns except the target column
# for column in data_filtered.columns:
#     if column != target_column and column != 'date':
#         data_filtered[column] = data_filtered[column].rolling(window=rolling_window, min_periods=1).mean()

# data_filtered.head()

In [17]:
# reduce the dimensionality of susceptible, infected, recovered, deceased in the data 7 days rolling mean for all the columns except the target


# Add rolling features
def add_rolling_features(df, window_size, columns, agg_funcs=None):
    if agg_funcs is None:
        agg_funcs = ["mean", "std", "min", "max"]
    added_features = {}
    for column in columns:
        for func in agg_funcs:
            roll_col_name = f"{column}_rolling_{window_size}_{func}"
            df[roll_col_name] = df[column].rolling(window_size).agg(func)
            if column not in added_features:
                added_features[column] = []
            added_features[column].append(roll_col_name)
    df.dropna(inplace=True)
    return df, added_features


window_size = 7
columns_to_roll = [
    "hospitalCases",
    "newAdmissions",
    "new_confirmed",
    "new_deceased",
    "susceptible",
    "active_cases",
    "recovered",
    "cumulative_deceased",
]
agg_funcs = ["mean"]

data_filtered, added_features = add_rolling_features(
    merged_data, window_size, columns_to_roll, agg_funcs
)

for column, features in added_features.items():
    logging.info(f"{column}: {', '.join(features)}")

2024-05-26 23:28:37,217 - INFO - hospitalCases: hospitalCases_rolling_7_mean
2024-05-26 23:28:37,217 - INFO - newAdmissions: newAdmissions_rolling_7_mean
2024-05-26 23:28:37,218 - INFO - new_confirmed: new_confirmed_rolling_7_mean
2024-05-26 23:28:37,219 - INFO - new_deceased: new_deceased_rolling_7_mean
2024-05-26 23:28:37,219 - INFO - susceptible: susceptible_rolling_7_mean
2024-05-26 23:28:37,220 - INFO - active_cases: active_cases_rolling_7_mean
2024-05-26 23:28:37,220 - INFO - recovered: recovered_rolling_7_mean
2024-05-26 23:28:37,221 - INFO - cumulative_deceased: cumulative_deceased_rolling_7_mean


In [18]:
# plot cumulative_deceased 
# fig = px.line(merged_data, x=merged_data.index, y="susceptible", title="Cumulative Deceased Cases")
# fig.show()

In [19]:
# Set the target variable and make it stationary
target = "covidOccupiedMVBeds"
seasonal_period = 7
auto_stationary = AutoStationaryTransformer(seasonal_period=seasonal_period)
data_stat = auto_stationary.fit_transform(merged_data[[target]], freq="D")
merged_data[target] = data_stat.values

# Ensure the index is a DateTimeIndex
merged_data.index = pd.to_datetime(merged_data.index)

In [20]:
# Filter data between the specified dates
start_date = "2020-04-27"
end_date = "2021-12-31"
merged_data = merged_data[start_date:end_date]

min_date = merged_data.index.min()
max_date = merged_data.index.max()

# Calculate the range of dates
date_range = max_date - min_date
logging.info(f"Data ranges from {min_date} to {max_date} ({date_range.days} days)")

2024-05-26 23:28:39,296 - INFO - Data ranges from 2020-05-07 00:00:00 to 2021-05-31 00:00:00 (389 days)


In [21]:
# # Calculate split points
# train_end = min_date + pd.DateOffset(months=14)
# val_end = train_end + pd.DateOffset(months=3)
# test_end = val_end + pd.DateOffset(months=2)

# train = merged_data[merged_data.index <= train_end]
# val = merged_data[(merged_data.index > train_end) & (merged_data.index <= val_end)]
# test = merged_data[merged_data.index > val_end]

# Calculate split points
train_end = min_date + pd.DateOffset(months=9)
val_end = train_end + pd.DateOffset(months=3)
test_end = val_end + pd.DateOffset(months=2)

train = merged_data[merged_data.index <= train_end]
val = merged_data[(merged_data.index > train_end) & (merged_data.index <= val_end)]
test = merged_data[merged_data.index > val_end]


# # Calculate split points
# total_days = date_range.days
# train_end = min_date + pd.Timedelta(days=int(total_days * 0.70))
# val_end = train_end + pd.Timedelta(days=int(total_days * 0.20))

# # Split the data into training, validation, and testing sets
# train = merged_data[merged_data.index <= train_end]
# val = merged_data[(merged_data.index > train_end) & (merged_data.index <= val_end)]
# test = merged_data[merged_data.index > val_end]

# Calculate the percentage of dates in each dataset
total_sample = len(merged_data)
train_sample = len(train) / total_sample * 100
val_sample = len(val) / total_sample * 100
test_sample = len(test) / total_sample * 100

print(f"Train: {train_sample:.2f}%, Validation: {val_sample:.2f}%, Test: {test_sample:.2f}%")
print(f"Train: {len(train)} samples, Validation: {len(val)} samples, Test: {len(test)} samples")
print(f"Max date in train: {train.index.max()}, Min date in validation: {val.index.min()}, Max date in test: {test.index.max()}")

Train: 71.03%, Validation: 22.82%, Test: 6.15%
Train: 277 samples, Validation: 89 samples, Test: 24 samples
Max date in train: 2021-02-07 00:00:00, Min date in validation: 2021-02-08 00:00:00, Max date in test: 2021-05-31 00:00:00


In [22]:
train.columns

Index(['covidOccupiedMVBeds', 'hospitalCases', 'newAdmissions',
       'new_confirmed', 'new_deceased', 'covidOccupiedMVBeds_lag_1',
       'covidOccupiedMVBeds_lag_2', 'covidOccupiedMVBeds_lag_3',
       'covidOccupiedMVBeds_lag_5', 'covidOccupiedMVBeds_lag_7',
       'covidOccupiedMVBeds_lag_14', 'covidOccupiedMVBeds_lag_21', 'month',
       'day', 'day_of_week', 'susceptible', 'exposed', 'active_cases',
       'recovered', 'cumulative_deceased', 'hospitalCases_rolling_7_mean',
       'newAdmissions_rolling_7_mean', 'new_confirmed_rolling_7_mean',
       'new_deceased_rolling_7_mean', 'susceptible_rolling_7_mean',
       'active_cases_rolling_7_mean', 'recovered_rolling_7_mean',
       'cumulative_deceased_rolling_7_mean'],
      dtype='object')

In [23]:
# Concatenate the DataFrames
sample_df = pd.concat([train, val, test])

# Convert all the feature columns to float32
sample_df = to_float32(sample_df)

columns_to_select = [
    "covidOccupiedMVBeds",
    "hospitalCases_rolling_7_mean",
    "hospitalCases_rolling_7_std",
    "newAdmissions_rolling_7_mean",
    "newAdmissions_rolling_7_std",
    "new_confirmed_rolling_7_mean",
    "new_confirmed_rolling_7_std",
    "new_deceased_rolling_7_mean",
    "new_deceased_rolling_7_std",
    "covidOccupiedMVBeds_lag_1",
    "covidOccupiedMVBeds_lag_2",
    "covidOccupiedMVBeds_lag_3",
    "covidOccupiedMVBeds_lag_5",
    "covidOccupiedMVBeds_lag_7",
    "covidOccupiedMVBeds_lag_14",
    "covidOccupiedMVBeds_lag_21",
    "month",
    "day",
    "day_of_week",
    # "susceptible",
    # "active_cases",
    # "recovered",
    # "cumulative_deceased",
]

pinn_features = [
    "covidOccupiedMVBeds",
    # "hospitalCases",
    # "newAdmissions",
    # "new_confirmed",
    # "new_deceased",
    "covidOccupiedMVBeds_lag_1",
    "covidOccupiedMVBeds_lag_2",
    "covidOccupiedMVBeds_lag_3",
    "covidOccupiedMVBeds_lag_5",
    "covidOccupiedMVBeds_lag_7",
    "covidOccupiedMVBeds_lag_14",
    "covidOccupiedMVBeds_lag_21",
    "month",
    "day",
    "day_of_week",
    # "susceptible",
    # "exposed",
    # "active_cases",
    # "recovered",
    # "cumulative_deceased",
    "hospitalCases_rolling_7_mean",
    "newAdmissions_rolling_7_mean",
    "new_confirmed_rolling_7_mean",
    "new_deceased_rolling_7_mean",
    # "susceptible_rolling_7_mean",
    "active_cases_rolling_7_mean",
    # "recovered_rolling_7_mean",
    # "cumulative_deceased_rolling_7_mean",
]

sample_df = sample_df[pinn_features]
cols = list(sample_df.columns)
cols.remove("covidOccupiedMVBeds")
sample_df = sample_df[cols + ["covidOccupiedMVBeds"]]
sample_df.head()

covidOccupiedMVBeds_lag_1  covidOccupiedMVBeds_lag_2  \
date                                                               
2020-05-07                      580.0                      565.0   
2020-05-08                      565.0                      580.0   
2020-05-09                      531.0                      565.0   
2020-05-10                      516.0                      531.0   
2020-05-11                      466.0                      516.0   

            covidOccupiedMVBeds_lag_3  covidOccupiedMVBeds_lag_5  \
date                                                               
2020-05-07                      587.0                      678.0   
2020-05-08                      565.0                      638.0   
2020-05-09                      580.0                      587.0   
2020-05-10                      565.0                      565.0   
2020-05-11                      531.0                      580.0   

            covidOccupiedMVBeds_lag_7  covidOccupiedMVBeds_lag_14  \
date                                                                
2020-05-07                      723.0                       897.0   
2020-05-08                      712.0                       836.0   
2020-05-09                      678.0                       868.0   
2020-05-10                      638.0                       831.0   
2020-05-11                      587.0                       800.0   

            covidOccupiedMVBeds_lag_21  month   day  day_of_week  \
date                                                               
2020-05-07                      1012.0    5.0   7.0          3.0   
2020-05-08                       982.0    5.0   8.0          4.0   
2020-05-09                       992.0    5.0   9.0          5.0   
2020-05-10                       991.0    5.0  10.0          6.0   
2020-05-11                      1019.0    5.0  11.0          0.0   

            hospitalCases_rolling_7_mean  newAdmissions_rolling_7_mean  \
date                                                                     
2020-05-07                   2322.285645                    181.857147   
2020-05-08                   2230.714355                    167.285721   
2020-05-09                   2164.857178                    158.000000   
2020-05-10                   2093.285645                    147.857147   
2020-05-11                   2029.285767                    136.714279   

            new_confirmed_rolling_7_mean  new_deceased_rolling_7_mean  \
date                                                                    
2020-05-07                    253.428574                    39.857143   
2020-05-08                    232.428574                    38.142857   
2020-05-09                    215.285721                    34.285713   
2020-05-10                    208.571426                    32.000000   
2020-05-11                    196.428574                    30.000000   

            active_cases_rolling_7_mean  recovered_rolling_7_mean  \
date                                                                
2020-05-07                 22720.355469              -1350.830200   
2020-05-08                 22666.935547              -1536.026855   
2020-05-09                 22687.269531              -1705.078369   
2020-05-10                 22683.523438               -760.473816   
2020-05-11                 22880.769531               -433.195709   

            covidOccupiedMVBeds  
date                             
2020-05-07            37.596306  
2020-05-08            36.875980  
2020-05-09            36.543293  
2020-05-10            35.444206  
2020-05-11            35.227757

In [24]:
# Prepare DataModule for PyTorch Lightning
datamodule = TimeSeriesDataModule(
    data=sample_df,
    n_val=val.shape[0],
    n_test=test.shape[0],
    window=7,  # 7 days window
    horizon=1,  # single step
    normalize="global",  # normalizing the data
    batch_size=32,
    num_workers=0,
)
datamodule.setup()

# Initialize pred_df
pred_df = test.copy()

In [25]:
# Function to train and evaluate models
def train_and_evaluate(model, rnn_config, datamodule, test, train, algorithm_name, metric_record, pred_df):
    trainer = pl.Trainer(
        min_epochs=5,
        max_epochs=200,
        accelerator="gpu",
        devices=1,
        callbacks=[EarlyStopping(monitor="valid_loss", patience=100)],
    )
    trainer.fit(model, datamodule)

    predictions = trainer.predict(model, datamodule.test_dataloader())
    predictions = torch.cat(predictions).squeeze().detach().numpy()
    predictions = predictions * datamodule.train.std + datamodule.train.mean
    actuals = test["covidOccupiedMVBeds"].values

    assert actuals.shape == predictions.shape, "Mismatch in shapes between actuals and predictions"

    metrics = {
        "Algorithm": algorithm_name,
        "MAE": mae(actuals, predictions),
        "MSE": mse(actuals, predictions),
        "MASE": mase(actuals, predictions, train["covidOccupiedMVBeds"].values),
        "Forecast Bias": forecast_bias(actuals, predictions),
    }

    value_formats = ["{}", "{:.4f}", "{:.4f}", "{:.4f}", "{:.2f}"]
    metrics = {
        key: format_.format(value)
        for key, value, format_ in zip(metrics.keys(), metrics.values(), value_formats)
    }

    pred_df_ = pd.DataFrame({algorithm_name: predictions}, index=test.index)
    pred_df = pred_df.join(pred_df_)
    metric_record.append(metrics)
    logging.info(metrics)
    return metric_record, pred_df

In [26]:
# Train Vanilla RNN
rnn_config = SingleStepRNNConfig(
    rnn_type="RNN",
    input_size=len(pinn_features),
    hidden_size=128,
    num_layers=10,
    bidirectional=False,
    learning_rate=1e-3,
)
model = SingleStepRNNModel(rnn_config)
algorithm_name = "Vanilla RNN"
metric_record, pred_df = train_and_evaluate(model, rnn_config, datamodule, test, train, algorithm_name, metric_record=[], pred_df=pred_df)

# Train Vanilla LSTM
rnn_config = SingleStepRNNConfig(
    rnn_type="LSTM",
    input_size=len(pinn_features),
    hidden_size=128,
    num_layers=10,
    bidirectional=False,
    learning_rate=1e-3,
)
model = SingleStepRNNModel(rnn_config)
algorithm_name = "Vanilla LSTM"
metric_record, pred_df = train_and_evaluate(model, rnn_config, datamodule, test, train, algorithm_name, metric_record, pred_df)

# Train Vanilla GRU
rnn_config = SingleStepRNNConfig(
    rnn_type="GRU",
    input_size=len(pinn_features),
    hidden_size=128,
    num_layers=10,
    bidirectional=False,
    learning_rate=1e-3,
)
model = SingleStepRNNModel(rnn_config)
algorithm_name = "Vanilla GRU"
metric_record, pred_df = train_and_evaluate(model, rnn_config, datamodule, test, train, algorithm_name, metric_record, pred_df)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Missing logger folder: /home/olarinoyem/Research/Multivate-forecasting/lightning_logs
2024-05-26 23:28:40.588708: I tensorflow/core/util/port.cc:110] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-05-26 23:28:40.634834: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-05-26 23:28:41.285081: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name | Type    | Params
---------------------------------
0 | rnn  | RNN     | 316 K 
1 | fc   | Linear  | 129   
2

Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]


Predicting: 0it [00:00, ?it/s]

2024-05-26 23:29:43,076 - INFO - {'Algorithm': 'Vanilla GRU', 'MAE': '48.9075', 'MSE': '2396.2716', 'MASE': '189.5807', 'Forecast Bias': '48.91'}


In [27]:
metric_record

[{'Algorithm': 'Vanilla RNN',
  'MAE': '8.6991',
  'MSE': '79.5372',
  'MASE': '33.7206',
  'Forecast Bias': '8.70'},
 {'Algorithm': 'Vanilla LSTM',
  'MAE': '20.9433',
  'MSE': '443.1611',
  'MASE': '81.1827',
  'Forecast Bias': '20.94'},
 {'Algorithm': 'Vanilla GRU',
  'MAE': '48.9075',
  'MSE': '2396.2716',
  'MASE': '189.5807',
  'Forecast Bias': '48.91'}]

In [28]:
# plot the forecast
forecast_columns = ["Vanilla RNN", "Vanilla LSTM", "Vanilla GRU"]
forecast_display_names = ["Vanilla RNN", "Vanilla LSTM", "Vanilla GRU"]
fig = plot_forecast(
    pred_df, forecast_columns, selected_area, forecast_display_names=forecast_display_names
)
fig.show()


In [29]:
param_bounds = {
    "rnn_type": ["RNN", "GRU", "LSTM"],
    "hidden_size": (32, 128),
    "num_layers": (5, 100),
    "bidirectional": [True, False]
}

initial_params = ["RNN", 32, 5, True]
initial_temp = 10

def objective(params):
    rnn_type, hidden_size, num_layers, bidirectional = params
    rnn_config = SingleStepRNNConfig(
        rnn_type=rnn_type,
        input_size=len(pinn_features),
        hidden_size=hidden_size,
        num_layers=num_layers,
        bidirectional=bidirectional,
        learning_rate=1e-3
    )
    model = SingleStepRNNModel(rnn_config)
    model.float()

    trainer = pl.Trainer(
        min_epochs=5,
        max_epochs=200,
        accelerator="gpu",
        devices=1,
        callbacks=[EarlyStopping(monitor="valid_loss", patience=100)],
    )
    trainer.fit(model, datamodule)
    
    shutil.rmtree("lightning_logs")

    predictions = trainer.predict(model, datamodule.test_dataloader())
    predictions = torch.cat(predictions).squeeze().detach().numpy()
    predictions = predictions * datamodule.train.std + datamodule.train.mean

    actuals = test["covidOccupiedMVBeds"].values

    assert actuals.shape == predictions.shape, "Mismatch in shapes between actuals and predictions"

    return np.mean(np.abs(actuals - predictions))

def neighbor(params):
    if len(params) == 4:
        rnn_type, hidden_size, num_layers, bidirectional = params
        hidden_size = np.random.randint(*param_bounds["hidden_size"])
        num_layers = np.random.randint(*param_bounds["num_layers"])
        rnn_type = np.random.choice(param_bounds["rnn_type"])
        bidirectional = bool(np.random.choice(param_bounds["bidirectional"]))
        return [rnn_type, hidden_size, num_layers, bidirectional]
    elif len(params) == 6:
        encoder_type, decoder_type, hidden_size, num_layers, bidirectional, decoder_use_all_hidden = params
        hidden_size = np.random.randint(*param_bounds["hidden_size"])
        num_layers = np.random.randint(*param_bounds["num_layers"])
        encoder_type = np.random.choice(param_bounds["encoder_type"])
        decoder_type = np.random.choice(param_bounds["decoder_type"])
        bidirectional = bool(np.random.choice(param_bounds["bidirectional"]))
        decoder_use_all_hidden = bool(np.random.choice(param_bounds["decoder_use_all_hidden"]))
        return [encoder_type, decoder_type, hidden_size, num_layers, bidirectional, decoder_use_all_hidden]

def simulated_annealing(objective, initial_params, initial_temp, neighbor, n_iter, cooling_rate=0.20, verbose=True):
    current_params = initial_params
    current_cost = objective(current_params)
    best_params = current_params
    best_cost = current_cost
    temp = initial_temp
    cost_history = []

    for i in range(n_iter):
        candidate_params = neighbor(current_params)
        candidate_cost = objective(candidate_params)

        acceptance_probability = np.exp(-abs(candidate_cost - current_cost) / temp)

        if candidate_cost < current_cost or np.random.uniform() < acceptance_probability:
            current_params = candidate_params
            current_cost = candidate_cost

            if current_cost < best_cost:
                best_params = current_params
                best_cost = current_cost

        temp *= cooling_rate
        cost_history.append(best_cost)

        logging.info(f"Iteration: {i+1}, Best Cost: {best_cost:.4f}, Current Cost: {current_cost:.4f}, Temperature: {temp:.4f}")
        
        # Break early if the minimum cost has been constant for over 30 iterations
        if i > 30 and np.all(np.isclose(cost_history[-30:], cost_history[-1])):
            break

    return best_cost, best_params, cost_history

n_iter = 200
cooling_rate = 0.95

best_cost, best_params, cost_history = simulated_annealing(
    objective, initial_params, initial_temp, neighbor, n_iter, cooling_rate
)

logging.info(f"Best Parameters: {best_params}, Best Cost: {best_cost}")

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(1, len(cost_history) + 1), y=cost_history, mode="lines"))
fig.update_layout(
    title="Simulated Annealing Optimization for Hyperparameter Tuning",
    xaxis_title="Iteration",
    yaxis_title="Best Cost",
    template="plotly_white",
)

fig.show()

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name | Type    | Params
---------------------------------
0 | rnn  | RNN     | 28.4 K
1 | fc   | Linear  | 65    
2 | loss | MSELoss | 0     
---------------------------------
28.4 K    Trainable params
0         Non-trainable params
28.4 K    Total params
0.114     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

2024-05-26 23:50:28,062 - INFO - Iteration: 19, Best Cost: 7.9336, Current Cost: 8.1048, Temperature: 3.7735
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name | Type    | Params
---------------------------------
0 | rnn  | GRU     | 3.5 M 
1 | fc   | Linear  | 169   
2 | loss | MSELoss | 0     
---------------------------------
3.5 M     Trainable params
0         Non-trainable params
3.5 M     Total params
14.034    Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

In [ ]:
nn_config = SingleStepRNNConfig(
    rnn_type=best_params[0],
    input_size=len(pinn_features),
    hidden_size=best_params[1],
    num_layers=best_params[2],
    bidirectional=best_params[3],
    learning_rate=1e-3,
)

model = SingleStepRNNModel(rnn_config)
algorithm_name = f"Optimized {rnn_config.rnn_type} (SA)"
metric_record, pred_df = train_and_evaluate(model, rnn_config, datamodule, test, train, algorithm_name, metric_record, pred_df)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name | Type    | Params
---------------------------------
0 | rnn  | GRU     | 950 K 
1 | fc   | Linear  | 129   
2 | loss | MSELoss | 0     
---------------------------------
950 K     Trainable params
0         Non-trainable params
950 K     Total params
3.804     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]


Predicting: 0it [00:00, ?it/s]

2024-05-26 16:15:16,379 - INFO - {'Algorithm': 'Optimized GRU (SA)', 'MAE': '11.7461', 'MSE': '142.0528', 'MASE': '45.5315', 'Forecast Bias': '11.75'}


In [ ]:
HORIZON = 1
WINDOW = 7

encoder_config = RNNConfig(
    input_size=len(pinn_features),
    hidden_size=128,
    num_layers=5,
    bidirectional=True
)

decoder_config = RNNConfig(
    input_size=len(pinn_features),
    hidden_size=128,
    num_layers=5,
    bidirectional=True
)

rnn2fc_config = Seq2SeqConfig(
    encoder_type="LSTM",
    decoder_type="FC",
    encoder_params=encoder_config,
    decoder_params={"window_size": WINDOW, "horizon": HORIZON},
    decoder_use_all_hidden=True,
    learning_rate=1e-3,
)

model = Seq2SeqModel(rnn2fc_config)
algorithm_name = "Seq2Seq LSTM"
metric_record, pred_df = train_and_evaluate(model, rnn2fc_config, datamodule, test, train, algorithm_name, metric_record, pred_df)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name    | Type    | Params
------------------------------------
0 | encoder | LSTM    | 1.7 M 
1 | decoder | Linear  | 1.8 K 
2 | loss    | MSELoss | 0     
------------------------------------
1.7 M     Trainable params
0         Non-trainable params
1.7 M     Total params
6.962     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]


Predicting: 0it [00:00, ?it/s]

2024-05-26 16:15:33,000 - INFO - {'Algorithm': 'Seq2Seq LSTM', 'MAE': '147.7331', 'MSE': '21866.1179', 'MASE': '572.6597', 'Forecast Bias': '147.73'}


In [ ]:
param_bounds = {
    "encoder_type": ["RNN", "GRU", "LSTM"],
    "decoder_type": ["FC"],
    "hidden_size": (32, 128),
    "num_layers": (5, 100),
    "bidirectional": [True, False],
    "decoder_use_all_hidden": [True, False],
}

initial_params = ["RNN", "FC", 32, 5, True, True]
initial_temp = 10

def objective(params):
    encoder_type, decoder_type, hidden_size, num_layers, bidirectional, decoder_use_all_hidden = params

    encoder_config = RNNConfig(
        input_size=len(pinn_features),
        hidden_size=hidden_size,
        num_layers=num_layers,
        bidirectional=bidirectional
    )

    decoder_config = RNNConfig(
        input_size=len(pinn_features),
        hidden_size=hidden_size,
        num_layers=num_layers,
        bidirectional=bidirectional
    )

    rnn2fc_config = Seq2SeqConfig(
        encoder_type=encoder_type,
        decoder_type=decoder_type,
        encoder_params=encoder_config,
        decoder_params={"window_size": WINDOW, "horizon": HORIZON},
        decoder_use_all_hidden=decoder_use_all_hidden,
        learning_rate=1e-3,
    )

    model = Seq2SeqModel(rnn2fc_config)

    trainer = pl.Trainer(
        min_epochs=5,
        max_epochs=200,
        accelerator="gpu",
        devices=1,
        callbacks=[EarlyStopping(monitor="valid_loss", patience=100)],
    )

    trainer.fit(model, datamodule)

    predictions = trainer.predict(model, datamodule.test_dataloader())
    predictions = torch.cat(predictions).squeeze().detach().numpy()
    predictions = predictions * datamodule.train.std + datamodule.train.mean

    actuals = test["covidOccupiedMVBeds"].values

    assert actuals.shape == predictions.shape, "Mismatch in shapes between actuals and predictions"

    return np.mean(np.abs(actuals - predictions))

best_cost, best_params, cost_history = simulated_annealing(
    objective, initial_params, initial_temp, neighbor, n_iter, cooling_rate
)

logging.info(f"Best Parameters: {best_params}, Best Cost: {best_cost}")

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(1, len(cost_history) + 1), y=cost_history, mode="lines"))
fig.update_layout(
    title="Simulated Annealing Optimization Seq2Seq for Hyperparameter Tuning",
    xaxis_title="Iteration",
    yaxis_title="Best Cost",
    template="plotly_white",
)

fig.show()

encoder_type, decoder_type, hidden_size, num_layers, bidirectional, decoder_use_all_hidden = best_params

encoder_config = RNNConfig(
    input_size=len(pinn_features),
    hidden_size=hidden_size,
    num_layers=num_layers,
    bidirectional=bidirectional
)

decoder_config = RNNConfig(
    input_size=len(pinn_features),
    hidden_size=hidden_size,
    num_layers=num_layers,
    bidirectional=bidirectional
)

rnn2fc_config = Seq2SeqConfig(
    encoder_type=encoder_type,
    decoder_type=decoder_type,
    encoder_params=encoder_config,
    decoder_params={"window_size": WINDOW, "horizon": HORIZON},
    decoder_use_all_hidden=decoder_use_all_hidden,
    learning_rate=1e-3,
)

model = Seq2SeqModel(rnn2fc_config)
algorithm_name = f"Optimized Seq2Seq {encoder_type} (SA)"
metric_record, pred_df = train_and_evaluate(model, rnn2fc_config, datamodule, test, train, algorithm_name, metric_record, pred_df)

shutil.rmtree("lightning_logs")

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]

  | Name    | Type    | Params
------------------------------------
0 | encoder | RNN     | 28.8 K
1 | decoder | Linear  | 449   
2 | loss    | MSELoss | 0     
------------------------------------
29.2 K    Trainable params
0         Non-trainable params
29.2 K    Total params
0.117     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1]


Predicting: 0it [00:00, ?it/s]

2024-05-26 17:31:11,019 - INFO - {'Algorithm': 'Optimized Seq2Seq RNN (SA)', 'MAE': '4.2773', 'MSE': '22.8866', 'MASE': '16.5803', 'Forecast Bias': '4.28'}


In [ ]:
# Save metrics
metric_df = pd.DataFrame(metric_record)
metric_df[["MAE", "MSE", "MASE", "Forecast Bias"]] = metric_df[
    ["MAE", "MSE", "MASE", "Forecast Bias"]
].astype("float32")

final_metric_file = f"reports/metrics/{selected_area}_final_metrics.csv"
metric_df.to_csv(final_metric_file, index=False)

# Save predictions
forecast_columns = [
    "Vanilla RNN", 
    "Vanilla LSTM", 
    "Vanilla GRU", 
    "Optimized GRU (SA)", 
    "Seq2Seq LSTM", 
    "Optimized Seq2Seq RNN (SA)",
]

forecast_display_names = [
    "Vanilla RNN", 
    "Vanilla LSTM", 
    "Vanilla GRU", 
    "Optimized GRU (SA)", 
    "Seq2Seq LSTM", 
    "Optimized Seq2Seq RNN (SA)",
]

comparison_fig = plot_forecast(
    pred_df,
    forecast_columns,
    selected_area,
    forecast_display_names,
    save_path=f"reports/figures/{selected_area}_forecast_comparison.pdf",
)
comparison_fig.show()

In [ ]:
pred_df.head(2)

covidOccupiedMVBeds  hospitalCases  newAdmissions  new_confirmed  \
date                                                                           
2021-05-08             8.321380          275.0             10          191.0   
2021-05-09             8.096463          274.0             16          287.0   

            new_deceased  covidOccupiedMVBeds_lag_1  \
date                                                  
2021-05-08           0.0                       62.0   
2021-05-09           0.0                       58.0   

            covidOccupiedMVBeds_lag_2  covidOccupiedMVBeds_lag_3  \
date                                                               
2021-05-08                       61.0                       65.0   
2021-05-09                       62.0                       61.0   

            covidOccupiedMVBeds_lag_5  covidOccupiedMVBeds_lag_7  ...  \
date                                                              ...   
2021-05-08                       70.0                       67.0  ...   
2021-05-09                       69.0                       69.0  ...   

            susceptible_rolling_7_mean  active_cases_rolling_7_mean  \
date                                                                  
2021-05-08                8.240214e+06                  5516.478171   
2021-05-09                8.239509e+06                  5385.604000   

            recovered_rolling_7_mean  cumulative_deceased_rolling_7_mean  \
date                                                                       
2021-05-08             708226.598571                        15645.732000   
2021-05-09             708167.270000                        15646.219143   

            Vanilla RNN  Vanilla LSTM  Vanilla GRU  Optimized GRU (SA)  \
date                                                                     
2021-05-08    -324.4375         24.75       39.625             17.1875   
2021-05-09    -323.8750         24.75       39.625             17.3125   

            Seq2Seq LSTM  Optimized Seq2Seq RNN (SA)  
date                                                  
2021-05-08      146.1875                      9.5625  
2021-05-09      146.7500                      9.5625  

[2 rows x 34 columns]

In [ ]:
pred_df.to_csv(f"reports/results/{selected_area}_predictions.csv")